In [1]:
import pyspark
from pyspark.sql import SparkSession

In [8]:
spark = SparkSession.builder \
    .master('local[*]') \
    .appName("SparkJOIN") \
    .getOrCreate()
    

22/07/05 17:35:27 WARN Utils: Your hostname, DESKTOP-KMM8QC4 resolves to a loopback address: 127.0.1.1; using 172.24.131.74 instead (on interface eth0)
22/07/05 17:35:27 WARN Utils: Set SPARK_LOCAL_IP if you need to bind to another address
22/07/05 17:35:29 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable
Using Spark's default log4j profile: org/apache/spark/log4j-defaults.properties
Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
22/07/05 17:35:31 WARN Utils: Service 'SparkUI' could not bind on port 4040. Attempting port 4041.
22/07/05 17:35:31 WARN Utils: Service 'SparkUI' could not bind on port 4041. Attempting port 4042.
22/07/05 17:35:31 WARN Utils: Service 'SparkUI' could not bind on port 4042. Attempting port 4043.
22/07/05 17:35:31 WARN Utils: Service 'SparkUI' could not bind on port 4043. Attempting port 4044.


In [15]:
# Reading green green_tripdata as parquet format year of 2020 & 2021 
green_parquet_path = "/home/thamizh/data/data/pq/green/*/*"
df_green = spark.read.parquet(green_parquet_path)

In [13]:
df_green.columns

['VendorID',
 'lpep_pickup_datetime',
 'lpep_dropoff_datetime',
 'store_and_fwd_flag',
 'RatecodeID',
 'PULocationID',
 'DOLocationID',
 'passenger_count',
 'trip_distance',
 'fare_amount',
 'extra',
 'mta_tax',
 'tip_amount',
 'tolls_amount',
 'ehail_fee',
 'improvement_surcharge',
 'total_amount',
 'payment_type',
 'trip_type',
 'congestion_surcharge']

In [14]:
len(df_green.columns)

20

In [16]:
# Register df as table, before query
df_green.registerTempTable('green')

In [34]:
# perform simple SQL query on green table

df_green_revenue = spark.sql("""
SELECT 
    date_trunc('hour', lpep_pickup_datetime) AS hour, 
    PULocationID AS zone,
    SUM(total_amount) AS amount,
    COUNT(1) AS number_records
FROM
    green
WHERE
    lpep_pickup_datetime >= '2020-01-01 00:00:00'
GROUP BY
    1, 2
""")

In [35]:
df_green_revenue.show()

+-------------------+----+------------------+--------------+
|               hour|zone|            amount|number_records|
+-------------------+----+------------------+--------------+
|2020-01-09 07:00:00|  74|1128.7699999999995|            80|
|2020-01-01 02:00:00| 244|             146.2|            10|
|2020-01-04 20:00:00|  82|1422.8399999999979|            80|
|2020-01-09 08:00:00|  95|            512.34|            27|
|2020-01-22 00:00:00|  97|54.480000000000004|             4|
|2020-01-17 18:00:00|  83|262.19000000000005|            12|
|2020-01-13 11:00:00|  74| 892.3299999999995|            66|
|2020-01-28 10:00:00|  35|            120.73|             4|
|2020-01-13 10:00:00|  82|282.83000000000004|            16|
|2020-01-12 22:00:00| 179|117.67999999999999|             5|
|2020-01-07 05:00:00|  69|            167.31|             6|
|2020-01-04 08:00:00| 101|57.849999999999994|             2|
|2020-01-21 10:00:00|  74| 1160.879999999999|            82|
|2020-01-23 15:00:00| 14

In [36]:
df_green_revenue \
    .repartition(20) \
    .write.parquet('/home/thamizh/data/data/report/revenue/green', mode='overwrite')

In [37]:
df_yellow = spark.read.parquet('/home/thamizh/data/data/pq/yellow/*/*')
df_yellow.registerTempTable('yellow')

In [38]:
df_yellow_revenue = spark.sql("""
SELECT 
    date_trunc('hour', tpep_pickup_datetime) AS hour, 
    PULocationID AS zone,
    SUM(total_amount) AS amount,
    COUNT(1) AS number_records
FROM
    yellow
WHERE
    tpep_pickup_datetime >= '2020-01-01 00:00:00'
GROUP BY
    1, 2
""")

In [39]:
df_yellow_revenue \
    .repartition(20) \
    .write.parquet('/home/thamizh/data/data/report/revenue/yellow', mode='overwrite')

In [40]:
df_green_revenue = spark.read.parquet('/home/thamizh/data/data/report/revenue/green')
df_yellow_revenue = spark.read.parquet('/home/thamizh/data/data/report/revenue/yellow')

In [41]:
df_green_revenue_tmp = df_green_revenue \
    .withColumnRenamed('amount', 'green_amount') \
    .withColumnRenamed('number_records', 'green_number_records')

df_yellow_revenue_tmp = df_yellow_revenue \
    .withColumnRenamed('amount', 'yellow_amount') \
    .withColumnRenamed('number_records', 'yellow_number_records')

In [42]:
df_join = df_green_revenue_tmp.join(df_yellow_revenue_tmp, on=['hour', 'zone'], how='outer')

In [52]:
df_join.show()

+-------------------+----+------------------+--------------------+------------------+---------------------+
|               hour|zone|      green_amount|green_number_records|     yellow_amount|yellow_number_records|
+-------------------+----+------------------+--------------------+------------------+---------------------+
|2020-01-01 00:00:00|  63|              51.9|                   2|              70.8|                    1|
|2020-01-01 01:00:00| 102|              null|                null|              29.0|                    1|
|2020-01-01 03:00:00| 123|              10.8|                   1|              null|                 null|
|2020-01-01 05:00:00| 114|              null|                null| 720.7500000000001|                   43|
|2020-01-01 05:00:00| 158|              null|                null| 634.3800000000001|                   26|
|2020-01-01 06:00:00| 152|             18.05|                   1|227.92000000000002|                    6|
|2020-01-01 07:00:00|  42|15

In [43]:
df_join.write.parquet('/home/thamizh/data/data/report/revenue/total', mode='overwrite')

In [44]:
df_join = spark.read.parquet('/home/thamizh/data/data/report/revenue/total')

In [45]:
df_join

DataFrame[hour: timestamp, zone: int, green_amount: double, green_number_records: bigint, yellow_amount: double, yellow_number_records: bigint]

In [47]:
df_zones = spark.read.parquet('/home/thamizh/zones/')

In [48]:
df_result = df_join.join(df_zones, df_join.zone == df_zones.LocationID)

In [53]:
df_result.show()

+-------------------+----+------------------+--------------------+------------------+---------------------+----------+---------+--------------------+------------+
|               hour|zone|      green_amount|green_number_records|     yellow_amount|yellow_number_records|LocationID|  Borough|                Zone|service_zone|
+-------------------+----+------------------+--------------------+------------------+---------------------+----------+---------+--------------------+------------+
|2020-01-01 00:00:00|  63|              51.9|                   2|              70.8|                    1|        63| Brooklyn|       Cypress Hills|   Boro Zone|
|2020-01-01 01:00:00| 102|              null|                null|              29.0|                    1|       102|   Queens|            Glendale|   Boro Zone|
|2020-01-01 03:00:00| 123|              10.8|                   1|              null|                 null|       123| Brooklyn|           Homecrest|   Boro Zone|
|2020-01-01 05:00:00| 

In [49]:
df_result.drop('LocationID', 'zone').write.parquet('tmp/revenue-zones')

In [50]:
!ls tmp/revenue-zones/

_SUCCESS
part-00000-5dd05154-3a60-4504-8232-50ef2e119e2c-c000.snappy.parquet
part-00001-5dd05154-3a60-4504-8232-50ef2e119e2c-c000.snappy.parquet
part-00002-5dd05154-3a60-4504-8232-50ef2e119e2c-c000.snappy.parquet
part-00003-5dd05154-3a60-4504-8232-50ef2e119e2c-c000.snappy.parquet
part-00004-5dd05154-3a60-4504-8232-50ef2e119e2c-c000.snappy.parquet
part-00005-5dd05154-3a60-4504-8232-50ef2e119e2c-c000.snappy.parquet
part-00006-5dd05154-3a60-4504-8232-50ef2e119e2c-c000.snappy.parquet


In [51]:
!parquet-tools show tmp/revenue-zones/part-00000-5dd05154-3a60-4504-8232-50ef2e119e2c-c000.snappy.parquet


+---------------------+----------------+------------------------+-----------------+-------------------------+---------------+----------------+
| hour                |   green_amount |   green_number_records |   yellow_amount |   yellow_number_records | Borough       | service_zone   |
|---------------------+----------------+------------------------+-----------------+-------------------------+---------------+----------------|
| 2019-12-31 18:30:00 |          51.9  |                      2 |    70.8         |                       1 | Brooklyn      | Boro Zone      |
| 2019-12-31 19:30:00 |         nan    |                    nan |    29           |                       1 | Queens        | Boro Zone      |
| 2019-12-31 21:30:00 |          10.8  |                      1 |   nan           |                     nan | Brooklyn      | Boro Zone      |
| 2019-12-31 23:30:00 |         nan    |                    nan |   720.75        |                      43 | Manhattan     | Yellow Zone    |

| 2020-07-20 10:30:00 |           8.8  |                      1 |   nan           |                     nan | Manhattan     | Boro Zone      |
| 2020-07-20 10:30:00 |          19.56 |                      1 |   nan           |                     nan | Bronx         | Boro Zone      |
| 2020-07-20 13:30:00 |          20.58 |                      1 |   nan           |                     nan | Bronx         | Boro Zone      |
| 2020-07-20 14:30:00 |         nan    |                    nan |    81.21        |                       4 | Manhattan     | Yellow Zone    |
| 2020-07-20 14:30:00 |         nan    |                    nan |     8.3         |                       1 | Manhattan     | Yellow Zone    |
| 2020-07-20 17:30:00 |          80.67 |                      1 |   nan           |                     nan | Bronx         | Boro Zone      |
| 2020-07-20 19:30:00 |         nan    |                    nan |    36           |                       1 | Brooklyn      | Boro Zone      |

| 2020-12-21 17:30:00 |         nan    |                    nan |   149.58        |                      11 | Manhattan     | Yellow Zone    |
| 2020-12-21 19:30:00 |         nan    |                    nan |   157.3         |                       3 | Unknown       | N/A            |
| 2020-12-21 23:30:00 |         nan    |                    nan |    90.26        |                       5 | Manhattan     | Yellow Zone    |
| 2020-12-21 23:30:00 |         nan    |                    nan |    40.8         |                       1 | Queens        | Boro Zone      |
| 2020-12-22 02:30:00 |         nan    |                    nan |   223.66        |                      12 | Manhattan     | Yellow Zone    |
| 2020-12-22 04:30:00 |         nan    |                    nan |    29           |                       1 | Bronx         | Boro Zone      |
| 2020-12-22 05:30:00 |          52.4  |                      1 |    43.26        |                       2 | Queens        | Boro Zone      |

| 2020-01-16 14:30:00 |          20    |                      1 |   nan           |                     nan | Brooklyn      | Boro Zone      |
| 2020-01-16 17:30:00 |          59.85 |                      5 |   115.98        |                       8 | Manhattan     | Boro Zone      |
| 2020-01-16 19:30:00 |          75.31 |                      6 |   120.46        |                      11 | Manhattan     | Boro Zone      |
| 2020-01-16 19:30:00 |         nan    |                    nan |  2803.17        |                     173 | Manhattan     | Yellow Zone    |
| 2020-01-16 20:30:00 |          66.27 |                      5 |   137.56        |                      11 | Manhattan     | Boro Zone      |
| 2020-01-16 23:30:00 |         nan    |                    nan |   157.72        |                       3 | Queens        | Boro Zone      |
| 2020-01-17 00:30:00 |          23.98 |                      1 |    85.87        |                       3 | Brooklyn      | Boro Zone      |

| 2020-06-24 22:30:00 |         227.4  |                      3 |    73.5         |                       1 | Staten Island | Boro Zone      |
| 2020-06-24 22:30:00 |         111.9  |                      2 |   nan           |                     nan | Bronx         | Boro Zone      |
| 2020-06-24 22:30:00 |         nan    |                    nan |    73.5         |                       1 | Queens        | Boro Zone      |
| 2020-06-24 23:30:00 |         nan    |                    nan |   173.8         |                       3 | Brooklyn      | Boro Zone      |
| 2020-06-25 02:30:00 |          46.5  |                      1 |   nan           |                     nan | Bronx         | Boro Zone      |
| 2020-06-25 03:30:00 |         nan    |                    nan |    62.36        |                       2 | Bronx         | Boro Zone      |
| 2020-06-25 05:30:00 |         nan    |                    nan |   338.78        |                      28 | Manhattan     | Yellow Zone    |

...

| 2020-01-09 18:30:00 |         nan    |                    nan |  3812.72        |                     219 | Manhattan     | Yellow Zone    |
| 2020-01-09 20:30:00 |         nan    |                    nan |   120.66        |                       6 | Manhattan     | Yellow Zone    |
| 2020-01-09 21:30:00 |         nan    |                    nan |   711.58        |                      33 | Manhattan     | Yellow Zone    |
| 2020-01-10 00:30:00 |          19.05 |                      1 |   378.23        |                      20 | Manhattan     | Boro Zone      |
| 2020-01-10 01:30:00 |         nan    |                    nan |    88.36        |                       3 | Bronx         | Boro Zone      |
| 2020-01-10 01:30:00 |         nan    |                    nan |   172.24        |                       5 | Bronx         | Boro Zone      |
| 2020-01-10 02:30:00 |          40.35 |                      2 |   188.24        |                       3 | Queens        | Boro Zone      |

| 2020-06-13 20:30:00 |         nan    |                    nan |    46.45        |                       1 | Bronx         | Boro Zone      |
| 2020-06-13 21:30:00 |         nan    |                    nan |    30.72        |                       3 | Manhattan     | Yellow Zone    |
| 2020-06-13 23:30:00 |         nan    |                    nan |    93.41        |                       1 | Bronx         | Boro Zone      |
| 2020-06-14 00:30:00 |         nan    |                    nan |   166.65        |                       2 | Manhattan     | Yellow Zone    |
| 2020-06-14 03:30:00 |           6.96 |                      1 |     4.8         |                       1 | Manhattan     | Boro Zone      |
| 2020-06-14 03:30:00 |         nan    |                    nan |   202.53        |                      14 | Manhattan     | Yellow Zone    |
| 2020-06-14 04:30:00 |         nan    |                    nan |   312.24        |                      20 | Manhattan     | Yellow Zone    |

| 2020-10-14 20:30:00 |         nan    |                    nan |    21.8         |                       1 | Manhattan     | Yellow Zone    |
| 2020-10-14 21:30:00 |         nan    |                    nan |    60           |                       1 | Queens        | Boro Zone      |
| 2020-10-14 22:30:00 |         nan    |                    nan |    47.31        |                       1 | Bronx         | Boro Zone      |
| 2020-10-15 01:30:00 |          31.35 |                      2 |   226.49        |                      10 | Queens        | Boro Zone      |
| 2020-10-15 01:30:00 |         nan    |                    nan |   274.29        |                      15 | Manhattan     | Yellow Zone    |
| 2020-10-15 07:30:00 |         nan    |                    nan |    36           |                       1 | Brooklyn      | Boro Zone      |
| 2020-10-15 07:30:00 |          10.3  |                      1 |   189.11        |                       5 | Brooklyn      | Boro Zone      |

| 2021-07-26 04:30:00 |         126.67 |                      9 |   nan           |                     nan | Manhattan     | Boro Zone      |
| 2021-07-26 07:30:00 |          31.06 |                      1 |   nan           |                     nan | Queens        | Boro Zone      |
| 2021-07-26 09:30:00 |         324.07 |                      8 |   nan           |                     nan | Queens        | Boro Zone      |
| 2021-07-26 11:30:00 |          44.86 |                      2 |   nan           |                     nan | Bronx         | Boro Zone      |
| 2021-07-26 13:30:00 |          10    |                      1 |   nan           |                     nan | Manhattan     | Boro Zone      |
| 2021-07-26 13:30:00 |          13.39 |                      1 |   nan           |                     nan | Bronx         | Boro Zone      |
| 2021-07-26 21:30:00 |          12.8  |                      1 |   nan           |                     nan | Manhattan     | Boro Zone      |

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

